In [2]:
import re
import sys
from time import sleep
from pprint import pprint
from functools import partial

import numpy as np
import optuna
try:
    import pandas as pd
except:
    pass


FILENAME = "main.cpp"

In [3]:
SEED = 0
N_TESTCASES = 200
!seq {SEED} {SEED+N_TESTCASES-1} > seeds.txt && cargo run --release --manifest-path ../tools/Cargo.toml --bin gen seeds.txt
!ls in

    Finished release [optimized] target(s) in 1.10s
     Running `/home/nagis/ahc003/tools/target/release/gen seeds.txt`
0000.txt  0025.txt  0050.txt  0075.txt	0100.txt  0125.txt  0150.txt  0175.txt
0001.txt  0026.txt  0051.txt  0076.txt	0101.txt  0126.txt  0151.txt  0176.txt
0002.txt  0027.txt  0052.txt  0077.txt	0102.txt  0127.txt  0152.txt  0177.txt
0003.txt  0028.txt  0053.txt  0078.txt	0103.txt  0128.txt  0153.txt  0178.txt
0004.txt  0029.txt  0054.txt  0079.txt	0104.txt  0129.txt  0154.txt  0179.txt
0005.txt  0030.txt  0055.txt  0080.txt	0105.txt  0130.txt  0155.txt  0180.txt
0006.txt  0031.txt  0056.txt  0081.txt	0106.txt  0131.txt  0156.txt  0181.txt
0007.txt  0032.txt  0057.txt  0082.txt	0107.txt  0132.txt  0157.txt  0182.txt
0008.txt  0033.txt  0058.txt  0083.txt	0108.txt  0133.txt  0158.txt  0183.txt
0009.txt  0034.txt  0059.txt  0084.txt	0109.txt  0134.txt  0159.txt  0184.txt
0010.txt  0035.txt  0060.txt  0085.txt	0110.txt  0135.txt  0160.txt  0185.txt
0011.txt  0036.txt  0

In [4]:
#!cp ../main.cpp ./

In [6]:
!g++ {FILENAME} -std=gnu++17 -Wall -Wextra -O2 -DONLINE_JUDGE -o {FILENAME}.out

main.cpp:451: warning: ignoring #pragma warning  [-Wunknown-pragmas]
  451 | #pragma warning( disable : 4146 )
      | 
main.cpp: In member function ‘void UltimateEstimator::Step()’:
main.cpp:1067:39: warning: comparison of integer expressions of different signedness: ‘signed char’ and ‘std::array<double, 60>::size_type’ {aka ‘long unsigned int’} [-Wsign-compare]
 1067 |   for (auto col = (signed char)0; col < data_x.size(); col++) {
      |                                   ~~~~^~~~~~~~~~~~~~~
main.cpp:1025:8: warning: unused variable ‘estimated_distance’ [-Wunused-variable]
 1025 |   auto estimated_distance = 0.0;
      |        ^~~~~~~~~~~~~~~~~~
main.cpp: In member function ‘void Explorer::Step()’:
main.cpp:1202:30: warning: narrowing conversion of ‘(((int)v.Explorer::Node::y) + 1)’ from ‘int’ to ‘signed char’ [-Wnarrowing]
 1202 |     const auto u = Node{ v.y + (i8)1, v.x, false };
      |                          ~~~~^~~~~~~
main.cpp:1215:35: warning: narrowing conversion of ‘(((

In [12]:
!cargo run --release --manifest-path ../tools/Cargo.toml --bin tester in/0000.txt $(pwd)/{FILENAME}.out 2>&1 | grep Score | sed -E s/[^0-9]+//


978777845


In [7]:
# ここでエラー出力は何かおかしいかもしれない


# パラメータ抽出
with open(FILENAME) as f:
    answer = f.read()


variables_optimize = []

for left, value, right, options in re.findall(r"^([^/\n]*=\s*)(.+?)(\s*;\s*//(?:.*\W)?OPTIMIZE(\W.*))$", answer, re.MULTILINE):
    name = left.replace("=", "").strip().split()[-1]
    
    searched = re.search(r".*\[(?P<min>.*),(?P<max>.*)\].*", options)
    if searched:
        min_value = max_value = None
        try:
            min_value = eval(searched.group("min"))
            max_value = eval(searched.group("max"))
            assert min_value <= max_value
        except Exception as e:
            print(f"searched={searched}", file=sys.stderr)
            print(e, file=sys.stderr)
            continue
        log = "LOG" in options  # 雑、直したほうが良い
        if type(min_value) != type(max_value):
            print(f"searched={searched}", file=sys.stderr)
            print("types not matched", file=sys.stderr)
            continue
        if isinstance(min_value, int):
            method = "suggest_int"
        elif isinstance(min_value, float):
            method = "suggest_float"
        else:
            print(f"searched={searched}", file=sys.stderr)
            print(f"unknown type ({type(min_value)})", file=sys.stderr)
            continue
        variables_optimize.append({
            "name": name,
            "method": method,
            "min": min_value,
            "max": max_value,
            "log": log,
            "left": left,
            "right": right,
        })
    elif searched := re.search(r".*\{(?P<choices>.*?)\}.*", options):
        choices = list(map(lambda x: x.strip(), searched.group("choices").split(",")))
        variables_optimize.append({
            "name": name,
            "method": "suggest_categorical",
            "choices": choices,
            "left": left,
            "right": right,
        })
    else:
        print(f"searched={searched}", file=sys.stderr)
        print(f"pattern was matched but options are incorrect.", file=sys.stderr)

print(len(variables_optimize), "variables were found.")
if globals().get("pd"):
    display(pd.DataFrame(variables_optimize))
else:
    pprint(variables_optimize)

8 variables were found.


name         method       min         max   log  \
0            LAMBDA  suggest_float     0.010     10000.0  True   
1      LASSO_LAMBDA  suggest_float  1000.000   1000000.0  True   
2         UCB1_COEF  suggest_float     1.000     10000.0  True   
3          UCB1_EPS  suggest_float     0.001        10.0  True   
4   TURNING_COST_50  suggest_float     1.000  10000000.0  True   
5  TURNING_COST_100  suggest_float     1.000    100000.0  True   
6  TURNING_COST_150  suggest_float     1.000    100000.0  True   
7  TURNING_COST_200  suggest_float     1.000    100000.0  True   

                                   left  \
0            constexpr double LAMBDA =    
1      constexpr double LASSO_LAMBDA =    
2         constexpr double UCB1_COEF =    
3          constexpr double UCB1_EPS =    
4   constexpr double TURNING_COST_50 =    
5  constexpr double TURNING_COST_100 =    
6  constexpr double TURNING_COST_150 =    
7  constexpr double TURNING_COST_200 =    

                                     right  
0  ;           // OPTIMIZE [1e-2, 1e4] LOG  
1        ;      // OPTIMIZE [1e3, 1e6] LOG  
2       ;       // OPTIMIZE [1e0, 1e4] LOG  
3   ;          // OPTIMIZE [1e-3, 1e1] LOG  
4           ;   // OPTIMIZE [1e0, 1e7] LOG  
5            ;  // OPTIMIZE [1e0, 1e5] LOG  
6            ;  // OPTIMIZE [1e0, 1e5] LOG  
7            ;  // OPTIMIZE [1e0, 1e5] LOG

In [15]:
def escape(string):  # 正規表現の中でそのまま使いたい文字列をエスケープ
    res = !echo '{string}' | sed -e 's/[]\/$*.^[]/\\&/g'
    return res[0]

def escape_sed(string):  # sed の置換後の文字列用のエスケープ
    res = !echo '{string}' | sed -e 's/[\/&]/\\&/g'
    return res[0]


def objective_with_index(trial, n_internal_parallel):
    index_parallel = trial.number % 10  # これ変数にする
    print(f"{index_parallel=}")
    
    parameters_changed_filename = f"{index_parallel}_{FILENAME}"
    directory_input = "./in"  # "/" をつけない
    
    !mkdir {index_parallel}_out
    !mkdir {index_parallel}_score
    !rm {index_parallel}_out/*
    !rm {index_parallel}_score/*
    
    # ファイル作成
    !cp {FILENAME} {parameters_changed_filename}
    sed_options = [f"-i {parameters_changed_filename}"]
    for variable in variables_optimize:
        if variable["method"] == "suggest_categorical":
            val =  trial.suggest_categorical(variable["name"], variable["choices"])
        else:
            val = getattr(trial, variable["method"])(variable["name"], variable["min"], variable["max"])
        left = variable["left"]
        right = variable["right"]
        sed_options.append(f"""-e 's/^{escape(left)}.*{escape(right)}$/{escape_sed(left)}{val}{escape_sed(right)}/'""")
    command_sed = f"sed {' '.join(sed_options)}"
    print(command_sed)
    !{command_sed}
    
    # コンパイル
    command_compile = f"g++ {parameters_changed_filename} -std=gnu++17 -O2 -DONLINE_JUDGE -o {parameters_changed_filename}.out 2> /dev/null"
    print(command_compile)
    !{command_compile}
    # 実行・採点コマンド (@ はファイル名)
    command_exec = (
        f"cargo run --release --manifest-path ../tools/Cargo.toml --bin tester {directory_input}/@ $(pwd)/{parameters_changed_filename}.out 2>&1 | grep Score | sed -E s/[^0-9]+// > ./{index_parallel}_score/@;"
        #f"./{parameters_changed_filename}.out < {directory_input}/@ > ./{index_parallel}_out/@;"
        #f"cargo run --release --manifest-path ./tools/Cargo.toml --bin vis {directory_input}/@ ./{index_parallel}_out/@ 2> /dev/null > ./{index_parallel}_score/@;"
    )
    # 並列実行 (sed はパスのディレクトリ部分を消してファイル名にしてる)
    !find {directory_input}/* | sed 's!^.*/!!' | xargs -I@ -P {n_internal_parallel} sh -c '{command_exec}'
    
    # 集計
    file_paths = !find ./{index_parallel}_score/*
    sum_score = 0
    for file_path in file_paths:  
        with open(file_path) as f:
            sum_score += int(f.read())
    return sum_score

In [16]:
storage_path = f"study.db"
storage = f"sqlite:///{storage_path}"
study_name = "study"
study = optuna.create_study(storage=storage, load_if_exists=True, study_name=study_name, direction="maximize")

def callback(study, trial):
    try:
        if study.best_value == trial.value:
            print(f"Updated! {study.best_value}")
            index_parallel = trial.number % 10
            parameters_changed_filename = f"{index_parallel}_{FILENAME}"
            !cp {parameters_changed_filename} 00000optimized.cpp
        print("callback ok")
    except:
        print(":(")

objective = partial(objective_with_index, n_internal_parallel=4)
study.optimize(objective, n_trials=3000, timeout=86400, n_jobs=4, callbacks=[callback])

[I 2021-05-28 03:48:26,549] Using an existing study with name 'study' instead of creating a new one.


index_parallel=4
index_parallel=5
index_parallel=6
index_parallel=7
rm: cannot remove '5_out/*': No such file or directory
rm: cannot remove '4_out/*': No such file or directory
rm: cannot remove '6_out/*': No such file or directory
rm: cannot remove '7_out/*': No such file or directory
rm: cannot remove '5_score/*': No such file or directory
rm: cannot remove '6_score/*': No such file or directory
rm: cannot remove '4_score/*': No such file or directory
rm: cannot remove '7_score/*': No such file or directory
sed -i 5_main.cpp -e 's/^constexpr double LAMBDA = .*;           \/\/ OPTIMIZE \[1e-2, 1e4\] LOG$/constexpr double LAMBDA = 9704.437211559143;           \/\/ OPTIMIZE [1e-2, 1e4] LOG/' -e 's/^constexpr double LASSO_LAMBDA = .*;      \/\/ OPTIMIZE \[1e3, 1e6\] LOG$/constexpr double LASSO_LAMBDA = 340981.1480349849;      \/\/ OPTIMIZE [1e3, 1e6] LOG/' -e 's/^constexpr double UCB1_COEF = .*;       \/\/ OPTIMIZE \[1e0, 1e4\] LOG$/constexpr double UCB1_COEF = 4078.10772832012;       \

[I 2021-05-28 03:49:29,487] Trial 5 finished with value: 188790557756.0 and parameters: {'LAMBDA': 9704.437211559143, 'LASSO_LAMBDA': 340981.1480349849, 'UCB1_COEF': 4078.10772832012, 'UCB1_EPS': 5.451478798562077, 'TURNING_COST_50': 1328302.874337738, 'TURNING_COST_100': 3830.4944683988692, 'TURNING_COST_150': 1717.1316990693256, 'TURNING_COST_200': 75293.48818633887}. Best is trial 5 with value: 188790557756.0.


Updated! 188790557756.0


[I 2021-05-28 03:49:29,581] Trial 4 finished with value: 188463978371.0 and parameters: {'LAMBDA': 5356.455930675361, 'LASSO_LAMBDA': 455948.41839970107, 'UCB1_COEF': 3392.336736223712, 'UCB1_EPS': 7.046510005018478, 'TURNING_COST_50': 1501684.2582405352, 'TURNING_COST_100': 65085.9755903717, 'TURNING_COST_150': 61347.31630846467, 'TURNING_COST_200': 6854.057466615408}. Best is trial 5 with value: 188790557756.0.
[I 2021-05-28 03:49:29,591] Trial 7 finished with value: 185501730253.0 and parameters: {'LAMBDA': 3960.9684889896757, 'LASSO_LAMBDA': 776312.1258339705, 'UCB1_COEF': 5115.42733876907, 'UCB1_EPS': 3.76918348200728, 'TURNING_COST_50': 4966559.04577776, 'TURNING_COST_100': 3225.866713388374, 'TURNING_COST_150': 2831.2499364824903, 'TURNING_COST_200': 36300.20813283702}. Best is trial 5 with value: 188790557756.0.
[I 2021-05-28 03:49:29,596] Trial 6 finished with value: 188601972632.0 and parameters: {'LAMBDA': 1238.797078686906, 'LASSO_LAMBDA': 418123.2950523647, 'UCB1_COEF': 43

...

callback ok
index_parallel=4
mkdir: cannot create directory ‘4_out’: File exists
mkdir: cannot create directory ‘4_score’: File exists
rm: cannot remove '4_out/*': No such file or directory
sed -i 3_main.cpp -e 's/^constexpr double LAMBDA = .*;           \/\/ OPTIMIZE \[1e-2, 1e4\] LOG$/constexpr double LAMBDA = 509.2105938825131;           \/\/ OPTIMIZE [1e-2, 1e4] LOG/' -e 's/^constexpr double LASSO_LAMBDA = .*;      \/\/ OPTIMIZE \[1e3, 1e6\] LOG$/constexpr double LASSO_LAMBDA = 49489.844153451384;      \/\/ OPTIMIZE [1e3, 1e6] LOG/' -e 's/^constexpr double UCB1_COEF = .*;       \/\/ OPTIMIZE \[1e0, 1e4\] LOG$/constexpr double UCB1_COEF = 465.37093281522436;       \/\/ OPTIMIZE [1e0, 1e4] LOG/' -e 's/^constexpr double UCB1_EPS = .*;          \/\/ OPTIMIZE \[1e-3, 1e1\] LOG$/constexpr double UCB1_EPS = 0.456820922771107;          \/\/ OPTIMIZE [1e-3, 1e1] LOG/' -e 's/^constexpr double TURNING_COST_50 = .*;   \/\/ OPTIMIZE \[1e0, 1e7\] LOG$/constexpr double TURNING_COST_50 = 3927149.5

[I 2021-05-28 14:32:08,515] Trial 2021 finished with value: 193858272047.0 and parameters: {'LAMBDA': 467.1826316857906, 'LASSO_LAMBDA': 18245.426108094547, 'UCB1_COEF': 939.9719333996723, 'UCB1_EPS': 0.7452678294737132, 'TURNING_COST_50': 3702500.2955305725, 'TURNING_COST_100': 24715.665710945374, 'TURNING_COST_150': 102.44188114956341, 'TURNING_COST_200': 9013.44251233323}. Best is trial 1996 with value: 194145425269.0.


callback ok
index_parallel=5
mkdir: cannot create directory ‘5_out’: File exists
mkdir: cannot create directory ‘5_score’: File exists
rm: cannot remove '5_out/*': No such file or directory


[W 2021-05-28 14:32:09,472] Trial 2025 failed because of the following error: IndexError('list index out of range')
Traceback (most recent call last):
  File "/home/nagis/anaconda3/lib/python3.8/site-packages/optuna/_optimize.py", line 217, in _run_trial
    value_or_values = func(trial)
  File "<ipython-input-15-8e2b889243bc>", line 32, in objective_with_index
    sed_options.append(f"""-e 's/^{escape(left)}.*{escape(right)}$/{escape_sed(left)}{val}{escape_sed(right)}/'""")
  File "<ipython-input-15-8e2b889243bc>", line 7, in escape_sed
    return res[0]
IndexError: list index out of range


KeyboardInterrupt: 

In [17]:
print(f"{study.best_value}")
pprint(study.best_params)

194145425269.0
{'LAMBDA': 164.79815141370864,
 'LASSO_LAMBDA': 17216.974925842333,
 'TURNING_COST_100': 20079.005861955284,
 'TURNING_COST_150': 1984.8049244192123,
 'TURNING_COST_200': 7837.489734778632,
 'TURNING_COST_50': 3616849.841967807,
 'UCB1_COEF': 502.42358003127214,
 'UCB1_EPS': 0.6984158334936159}


[I 2021-05-28 14:32:51,576] Trial 2023 finished with value: 193637152223.0 and parameters: {'LAMBDA': 509.2105938825131, 'LASSO_LAMBDA': 49489.844153451384, 'UCB1_COEF': 465.37093281522436, 'UCB1_EPS': 0.456820922771107, 'TURNING_COST_50': 3927149.526021245, 'TURNING_COST_100': 24242.142210669437, 'TURNING_COST_150': 11227.3503965273, 'TURNING_COST_200': 7271.819006889496}. Best is trial 1996 with value: 194145425269.0.


callback ok


[I 2021-05-28 14:32:52,239] Trial 2024 finished with value: 193166339923.0 and parameters: {'LAMBDA': 824.1631865136442, 'LASSO_LAMBDA': 74427.53876082989, 'UCB1_COEF': 422.3085797213794, 'UCB1_EPS': 0.37122635266655807, 'TURNING_COST_50': 3868612.7299372456, 'TURNING_COST_100': 24268.849697324225, 'TURNING_COST_150': 8596.72411587431, 'TURNING_COST_200': 9089.935904810727}. Best is trial 1996 with value: 194145425269.0.


callback ok
